In [ ]:
import essentia
import essentia.standard as es
import json

In [ ]:
import yt_dlp
import IPython.display as ipd

def download_mp3(url, output_name="song"):
    ydl_opts = {
        'format': 'bestaudio/best',
        'outtmpl': output_name,
        'ffmpeg_location': '/opt/homebrew/bin/ffmpeg', 
        'postprocessors': [{
            'key': 'FFmpegExtractAudio',
            'preferredcodec': 'mp3',
            'preferredquality': '192',
        }],
    }
    
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([url])

# Example usage
download_mp3("https://youtu.be/tKUDVBNgTE0?si=ntEA7VTLMRHQbz9d")

# Play the downloaded MP3 file
ipd.Audio("song.mp3")

[youtube] Extracting URL: https://youtu.be/tKUDVBNgTE0?si=ntEA7VTLMRHQbz9d
[youtube] tKUDVBNgTE0: Downloading webpage
[youtube] tKUDVBNgTE0: Downloading tv client config
[youtube] tKUDVBNgTE0: Downloading player 179bab65-main
[youtube] tKUDVBNgTE0: Downloading tv player API JSON
[youtube] tKUDVBNgTE0: Downloading ios player API JSON
[youtube] tKUDVBNgTE0: Downloading m3u8 information
[info] tKUDVBNgTE0: Downloading 1 format(s): 251
[download] Destination: song
[download] 100% of    3.19MiB in 00:00:00 at 8.55MiB/s     
[ExtractAudio] Destination: song.mp3
Deleting original file song (pass -k to keep)


In [ ]:
import subprocess
import json
from collections import defaultdict
from essentia.standard import MusicExtractor

# Step 1: Convert MP3 to WAV
def convert_to_wav(input_file, output_file="temp.wav"):
    subprocess.run(["ffmpeg", "-y", "-i", input_file, output_file], check=True)

# Step 2: Load classifier labels from file
def load_classifier_labels(filename="classifiers.txt"):
    with open(filename, "r") as f:
        return set(line.strip() for line in f if line.strip())

# Step 3: Filter extracted features by classifier keys
def filter_keys_by_classifier_list(pool, classifier_keys):
    def nested_dict():
        return defaultdict(nested_dict)

    root = nested_dict()
    for key in pool.descriptorNames():
        if any(key.startswith(label) for label in classifier_keys):
            parts = key.split('.')
            current = root
            for part in parts[:-1]:
                current = current[part]
            val = pool[key]
            current[parts[-1]] = val.tolist() if hasattr(val, 'tolist') else val

    return json.loads(json.dumps(root))  # Convert nested defaultdict to regular dict

# Step 4: Extract features and save filtered output
def extract_filtered_features(mp3_path, classifiers_path="classifiers.txt", output_json="filtered_features.json"):
    wav_path = "temp.wav"
    convert_to_wav(mp3_path, wav_path)

    # Extract features
    extractor = MusicExtractor()
    features, audio = extractor(wav_path)

    # Filter features
    classifier_keys = load_classifier_labels(classifiers_path)
    filtered = filter_keys_by_classifier_list(features, classifier_keys)

    # Save JSON
    with open(output_json, "w") as f:
        json.dump(filtered, f, indent=2)

    print(f"✅ Saved filtered features to: {output_json}")


extract_filtered_features("song.mp3", "/classifiers.txt", "features.json")

ffmpeg version 7.1.1 Copyright (c) 2000-2025 the FFmpeg developers
  built with Apple clang version 16.0.0 (clang-1600.0.26.6)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1.1_1 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libspeex

FileNotFoundError: [Errno 2] No such file or directory: 'classifiers.txt'